In [1]:
%load_ext tensorboard
# Clear any logs from previous runs
!rm -rf ./logs/

In [2]:
import tensorflow as tf
from tensorboard.plugins.hparams import api as hp
import numpy as np
from sklearn.preprocessing import StandardScaler
import pandas as pd
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input,Conv2D,MaxPooling2D,UpSampling2D, Dense
from sklearn.preprocessing import StandardScaler, MinMaxScaler


In [3]:
file = 'data/pantheon.txt'
data = pd.read_csv(file, sep = " " ,usecols=['zcmb', 'zhel', 'mb', 'dmb'] )
data.head()
# plt.show()

syscov = np.loadtxt('data/pantheon_errors.txt',skiprows=1).reshape((1048,1048))

dataFull = np.concatenate([data.values, syscov], axis=1)

x = dataFull[:, 0]
Y = dataFull[:, 1:]

print(np.shape(dataFull))
randomize = np.random.permutation(len(data.values))

X = x[randomize]
y = Y[randomize]
print(randomize)

scalerx = StandardScaler()
scalerx.fit(X.reshape(-1,1))
X = scalerx.transform(X.reshape(-1,1))

scalery = StandardScaler()
scalery.fit(Y)
y = scalery.transform(y)

split = 0.8
ntrain = int(split * len(X))
indx = [ntrain]
X_train, X_test = np.split(X, indx)
y_train, y_test = np.split(y, indx)

(1048, 1052)
[ 436 1002  920 ... 1030  907  626]


In [4]:
callbacks = [tf.keras.callbacks.EarlyStopping(monitor='val_loss', mode='min',
                                   min_delta=0,
                                   patience=10,
                                   restore_best_weights=True)]



In [5]:
HP_NUM_UNITS1 = hp.HParam('num_units1', hp.Discrete([300, 400,500,600]))
HP_NUM_UNITS2 = hp.HParam('num_units2', hp.Discrete([200,300, 400]))
HP_NUM_UNITS3 = hp.HParam('num_units3', hp.Discrete([100, 200]))
HP_NUM_UNITS4 = hp.HParam('num_units4', hp.Discrete([50, 100]))
# HP_DROPOUT = hp.HParam('dropout', hp.RealInterval(0.0, 0.2))
# HP_OPTIMIZER = hp.HParam('optimizer', hp.Discrete(['adam', 'sgd']))
# HP_OPTIMIZER = hp.HParam('optimizer', hp.Discrete(['adam', 'Adadelta']))
# HP_OPTIMIZER = hp.HParam('optimizer', hp.Discrete(['adam']))
HP_BATCHSIZE = hp.HParam('batch_size', hp.Discrete([32,64]))

In [6]:
# sess = tf.Session()
# writer = tf.summary.FileWriter("/tmp/tfvgg", sess.graph)
# init = tf.initialize_all_variables()
# sess.run(init)
# with tf.summary.create_file_writer('logs/hparam_tuning').as_default():
#     hp.hparams_config(
#         hparams=[HP_NUM_UNITS1, HP_NUM_UNITS2, HP_NUM_UNITS3, HP_NUM_UNITS4,
#                  HP_OPTIMIZER, HP_BATCHSIZE],
#         metrics=[hp.Metric('loss', display_name="Loss")])

In [7]:
# METRIC_ACCURACY = 'accuracy'
with tf.summary.create_file_writer('logs/hparam_tuning').as_default():
# with tf.summary.FileWriter('logs/hparam_tuning', sess.graph):
#     init = tf.initialize_all_variables()
#     sess.run(init)
    hp.hparams_config(
        hparams=[HP_NUM_UNITS1, HP_NUM_UNITS2, HP_NUM_UNITS3, HP_NUM_UNITS4, HP_BATCHSIZE],
        metrics=[hp.Metric('loss', display_name="Loss")])

In [8]:
def autoencoder(input_z, hparams):
    #encoder
    #input = 28 x 28 x 1 (wide and thin)
    efirst = Dense(hparams[HP_NUM_UNITS1], activation='relu', input_shape=(1,))(input_z)
    ehidden = Dense(hparams[HP_NUM_UNITS2], activation='relu')(efirst)
    elast = Dense(hparams[HP_NUM_UNITS3], activation='relu')(ehidden)
    coded = Dense(hparams[HP_NUM_UNITS4], activation='relu')(elast)
    #decoder 
    dfirst = Dense(hparams[HP_NUM_UNITS3], activation='relu')(coded)
    dhidden = Dense(hparams[HP_NUM_UNITS2], activation='relu')(dfirst)
    dlast = Dense(hparams[HP_NUM_UNITS1], activation='relu')(dhidden)
    decoded = Dense(1051, activation='relu')(dlast)
    
    return decoded

In [9]:
epochs = 200
input_z = Input(shape = (1,))


In [10]:
def train_test_model(hparams):
    model = Model(input_z, autoencoder(input_z, hparams))  
                              
    model.compile(
#             optimizer=hparams[HP_OPTIMIZER],
            optimizer='adam',
            loss='mean_squared_error',
            metrics=['mean_squared_error']
          )
    # Run with 1 epoch to speed things up for demo purposes
    # model.fit(x_train, y_train, epochs=1, callbacks=callbacks) 
    # _, loss = model.evaluate(x_test, y_test)
    model.fit(X_train, y_train, epochs=epochs, 
              batch_size=hparams[HP_BATCHSIZE], callbacks=callbacks) 
    _, loss = model.evaluate(X_test, y_test)


    return loss
    

In [11]:
def run(run_dir, hparams):
    with tf.summary.create_file_writer(run_dir).as_default():
#     with tf.summary.FileWriter(run_dir):
        hp.hparams(hparams)  # record the values used in this trial
        loss = train_test_model(hparams)
        tf.summary.scalar("loss", loss, step=1)

In [12]:
session_num = 0

for batch_size in HP_BATCHSIZE.domain.values:
    for num_units1 in HP_NUM_UNITS1.domain.values:
        for num_units2 in HP_NUM_UNITS2.domain.values:
            for num_units3 in HP_NUM_UNITS3.domain.values:
                for num_units4 in HP_NUM_UNITS4.domain.values:
#       for dropout_rate in (HP_DROPOUT.domain.min_value, HP_DROPOUT.domain.max_value):
#                     for optimizer in HP_OPTIMIZER.domain.values:
                    hparams = {
                      HP_NUM_UNITS1: num_units1,
                      HP_NUM_UNITS2: num_units2,
                      HP_NUM_UNITS3: num_units3,
                      HP_NUM_UNITS4: num_units4,
                    #                       HP_DROPOUT: dropout_rate,
#                       HP_OPTIMIZER: optimizer,
                      HP_BATCHSIZE: batch_size
                    }
                    run_name = "run-%d" % session_num
                    print('--- Starting trial: %s' % run_name)
                    print({h.name: hparams[h] for h in hparams})
                    run('logs/hparam_tuning/' + run_name, hparams)
                    session_num += 1

--- Starting trial: run-0
{'num_units1': 300, 'num_units2': 200, 'num_units3': 100, 'num_units4': 50, 'batch_size': 32}
Epoch 1/200
27/27 [==============================] - 0s 3ms/step - loss: 0.9655 - mean_squared_error: 0.9655
Epoch 2/200
27/27 [==============================] - 0s 3ms/step - loss: 0.8838 - mean_squared_error: 0.8838
Epoch 3/200
27/27 [==============================] - 0s 3ms/step - loss: 0.7858 - mean_squared_error: 0.7858
Epoch 4/200
27/27 [==============================] - 0s 4ms/step - loss: 0.7621 - mean_squared_error: 0.7621
Epoch 5/200
27/27 [==============================] - 0s 4ms/step - loss: 0.7513 - mean_squared_error: 0.7513
Epoch 6/200
27/27 [==============================] - 0s 4ms/step - loss: 0.7414 - mean_squared_error: 0.7414
Epoch 7/200
27/27 [==============================] - 0s 4ms/step - loss: 0.7246 - mean_squared_error: 0.7246
Epoch 8/200
27/27 [==============================] - 0s 4ms/step - loss: 0.7172 - mean_squared_error: 0.7172
Epoch 9/

Epoch 25/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6928 - mean_squared_error: 0.6928
Epoch 26/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6928 - mean_squared_error: 0.6928
Epoch 27/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6959 - mean_squared_error: 0.6959
Epoch 28/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6893 - mean_squared_error: 0.6893
Epoch 29/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6883 - mean_squared_error: 0.6883
Epoch 30/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6872 - mean_squared_error: 0.6872
Epoch 31/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6904 - mean_squared_error: 0.6904
Epoch 32/200
27/27 [==============================] - 0s 3ms/step - loss: 0.7002 - mean_squared_error: 0.7002
Epoch 33/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6871 - mean_squared_error: 0.6871
Epoch 34/2

27/27 [==============================] - 0s 8ms/step - loss: 0.6738 - mean_squared_error: 0.6738
Epoch 50/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6749 - mean_squared_error: 0.6749
Epoch 51/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6761 - mean_squared_error: 0.6761
Epoch 52/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6716 - mean_squared_error: 0.6716
Epoch 53/200
27/27 [==============================] - 0s 6ms/step - loss: 0.6731 - mean_squared_error: 0.6731
Epoch 54/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6723 - mean_squared_error: 0.6723
Epoch 55/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6739 - mean_squared_error: 0.6739
Epoch 56/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6790 - mean_squared_error: 0.6790
Epoch 57/200
27/27 [==============================] - 0s 8ms/step - loss: 0.6739 - mean_squared_error: 0.6739
Epoch 58/200
27/27 [===

27/27 [==============================] - 0s 4ms/step - loss: 0.6661 - mean_squared_error: 0.6661
Epoch 74/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6620 - mean_squared_error: 0.6620
Epoch 75/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6614 - mean_squared_error: 0.6614
Epoch 76/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6604 - mean_squared_error: 0.6604
Epoch 77/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6606 - mean_squared_error: 0.6606
Epoch 78/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6595 - mean_squared_error: 0.6595
Epoch 79/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6597 - mean_squared_error: 0.6597
Epoch 80/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6588 - mean_squared_error: 0.6588
Epoch 81/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6757 - mean_squared_error: 0.6757
Epoch 82/200
27/27 [===

27/27 [==============================] - 0s 4ms/step - loss: 0.6565 - mean_squared_error: 0.6565
Epoch 98/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6525 - mean_squared_error: 0.6525
Epoch 99/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6514 - mean_squared_error: 0.6514
Epoch 100/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6825 - mean_squared_error: 0.6825
Epoch 101/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6640 - mean_squared_error: 0.6640
Epoch 102/200
27/27 [==============================] - 0s 5ms/step - loss: 0.6560 - mean_squared_error: 0.6560
Epoch 103/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6512 - mean_squared_error: 0.6512
Epoch 104/200
27/27 [==============================] - 0s 3ms/step - loss: 0.6542 - mean_squared_error: 0.6542
Epoch 105/200
27/27 [==============================] - 0s 4ms/step - loss: 0.6488 - mean_squared_error: 0.6488
Epoch 106/200
27/

...

14/14 [==============================] - 0s 8ms/step - loss: 0.6508 - mean_squared_error: 0.6508
Epoch 105/200
14/14 [==============================] - 0s 9ms/step - loss: 0.6477 - mean_squared_error: 0.6477
Epoch 106/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6473 - mean_squared_error: 0.6473
Epoch 107/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6480 - mean_squared_error: 0.6480
Epoch 108/200
14/14 [==============================] - 0s 10ms/step - loss: 0.6492 - mean_squared_error: 0.6492
Epoch 109/200
14/14 [==============================] - 0s 9ms/step - loss: 0.6509 - mean_squared_error: 0.6509
Epoch 110/200
14/14 [==============================] - 0s 10ms/step - loss: 0.6484 - mean_squared_error: 0.6484
Epoch 111/200
14/14 [==============================] - 0s 10ms/step - loss: 0.6459 - mean_squared_error: 0.6459
Epoch 112/200
14/14 [==============================] - 0s 10ms/step - loss: 0.6445 - mean_squared_error: 0.6445
Epoch 113/2

14/14 [==============================] - 0s 8ms/step - loss: 0.6429 - mean_squared_error: 0.6429
Epoch 129/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6407 - mean_squared_error: 0.6407
Epoch 130/200
14/14 [==============================] - 0s 9ms/step - loss: 0.6404 - mean_squared_error: 0.6404
Epoch 131/200
14/14 [==============================] - 0s 9ms/step - loss: 0.6416 - mean_squared_error: 0.6416
Epoch 132/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6426 - mean_squared_error: 0.6426
Epoch 133/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6427 - mean_squared_error: 0.6427
Epoch 134/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6441 - mean_squared_error: 0.6441
Epoch 135/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6442 - mean_squared_error: 0.6442
Epoch 136/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6413 - mean_squared_error: 0.6413
Epoch 137/200
1

14/14 [==============================] - 0s 8ms/step - loss: 0.6447 - mean_squared_error: 0.6447
Epoch 153/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6406 - mean_squared_error: 0.6406
Epoch 154/200
14/14 [==============================] - 0s 9ms/step - loss: 0.6388 - mean_squared_error: 0.6388
Epoch 155/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6360 - mean_squared_error: 0.6360
Epoch 156/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6350 - mean_squared_error: 0.6350
Epoch 157/200
14/14 [==============================] - 0s 8ms/step - loss: 0.6369 - mean_squared_error: 0.6369
Epoch 158/200
14/14 [==============================] - 0s 9ms/step - loss: 0.6380 - mean_squared_error: 0.6380
Epoch 159/200
14/14 [==============================] - 0s 9ms/step - loss: 0.6346 - mean_squared_error: 0.6346
Epoch 160/200
14/14 [==============================] - 0s 10ms/step - loss: 0.6341 - mean_squared_error: 0.6341
Epoch 161/200


14/14 [==============================] - 0s 10ms/step - loss: 0.6314 - mean_squared_error: 0.6314
Epoch 177/200


KeyboardInterrupt: 

In [ ]:
!kill 24089
%tensorboard --logdir logs/hparam_tuning